In [ ]:
# 读取配置
from config_jingbo import *
# from config_tansuanli import *
# from config_juxiting import *
from lib.dataread import *
from lib.tools import *
from models.nerulforcastmodels import ex_Model,model_losss,brent_export_pdf,tansuanli_export_pdf,pp_export_pdf

import glob
import torch
torch.set_float32_matmul_precision("high")

sqlitedb = SQLiteHandler(db_name) 
sqlitedb.connect()


signature = BinanceAPI(APPID, SECRET)
etadata = EtaReader(signature=signature,
                        classifylisturl = classifylisturl,
                        classifyidlisturl=classifyidlisturl,
                        edbcodedataurl=edbcodedataurl,
                        edbcodelist=edbcodelist,
                        edbdatapushurl=edbdatapushurl,
                        edbdeleteurl=edbdeleteurl,
                        edbbusinessurl=edbbusinessurl
                        )
# 获取数据
if is_eta:
    # eta数据
    logger.info('从eta获取数据...')
    signature = BinanceAPI(APPID, SECRET)
    etadata = EtaReader(signature=signature,
                                classifylisturl = classifylisturl,
                                classifyidlisturl=classifyidlisturl,
                                edbcodedataurl=edbcodedataurl,
                                edbcodelist=edbcodelist,
                                edbdatapushurl=edbdatapushurl,
                                edbdeleteurl=edbdeleteurl,
                                edbbusinessurl=edbbusinessurl,
                                )

    df_zhibiaoshuju,df_zhibiaoliebiao = etadata.get_eta_api_yuanyou_data(data_set=data_set,dataset=dataset)  # 原始数据，未处理
    # df_zhibiaoshuju,df_zhibiaoliebiao =  etadata.get_eta_api_pp_data(data_set=data_set,dataset=dataset)  # 原始数据，未处理

    
    # 数据处理
    df = datachuli(df_zhibiaoshuju,df_zhibiaoliebiao,y = y,dataset=dataset,add_kdj=add_kdj,is_timefurture=is_timefurture,end_time=end_time) 

else:
    logger.info('读取本地数据：'+os.path.join(dataset,data_set))
    df = getdata(filename=os.path.join(dataset,data_set),y=y,dataset=dataset,add_kdj=add_kdj,is_timefurture=is_timefurture,end_time=end_time)  # 原始数据，未处理

# 更改预测列名称
df.rename(columns={y:'y'},inplace=True)
    
if is_edbnamelist:
    df = df[edbnamelist]     
df.to_csv(os.path.join(dataset,'指标数据.csv'), index=False)
# 保存最新日期的y值到数据库
# 取第一行数据存储到数据库中
first_row = df[['ds','y']].tail(1)
# 将最新真实值保存到数据库
if not sqlitedb.check_table_exists('trueandpredict'):
    first_row.to_sql('trueandpredict',sqlitedb.connection,index=False)
else:
    for row in first_row.itertuples(index=False):
        row_dict = row._asdict()
        check_query = sqlitedb.select_data('trueandpredict',where_condition = f"ds = '{row.ds}'")
        if len(check_query) > 0:
            set_clause = ", ".join([f"{key} = '{value}'" for key, value in row_dict.items()])
            sqlitedb.update_data('trueandpredict',set_clause,where_condition = f"ds = '{row.ds}'")
            continue
        sqlitedb.insert_data('trueandpredict',tuple(row_dict.values()),columns=row_dict.keys())

import datetime
# 判断当前日期是不是周一
is_weekday = datetime.datetime.now().weekday() == 3
if is_weekday:
    logger.info('今天是周一，更新预测模型')
    # 计算最近20天预测残差最低的模型名称

    model_results = sqlitedb.select_data('trueandpredict',order_by = "ds DESC",limit = "20")
    model_results = model_results.dropna()
    modelnames  = model_results.columns.to_list()[2:] 
    for col in model_results[modelnames].select_dtypes(include=['object']).columns:
        model_results[col] = model_results[col].astype(np.float32)
    # 计算每个预测值与真实值之间的偏差率
    for model in modelnames:
        model_results[f'{model}_abs_error_rate'] = abs(model_results['y'] - model_results[model]) / model_results['y']

    # 获取每行对应的最小偏差率值
    min_abs_error_rate_values = model_results.apply(lambda row: row[[f'{model}_abs_error_rate' for model in modelnames]].min(), axis=1)
    # 获取每行对应的最小偏差率值对应的列名
    min_abs_error_rate_column_name = model_results.apply(lambda row: row[[f'{model}_abs_error_rate' for model in modelnames]].idxmin(), axis=1)
    # 将列名索引转换为列名
    min_abs_error_rate_column_name = min_abs_error_rate_column_name.map(lambda x: x.split('_')[0])
    # 取出现次数最多的模型名称
    most_common_model = min_abs_error_rate_column_name.value_counts().idxmax()
    logger.info(f"最近20天预测残差最低的模型名称：{most_common_model}")

    # 保存结果到数据库
    
    if not sqlitedb.check_table_exists('most_model'):
        sqlitedb.create_table('most_model',columns="ds datetime, most_common_model TEXT")
    sqlitedb.insert_data('most_model',(datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S'),most_common_model,),columns=('ds','most_common_model',))






if is_corr:
    df = corr_feature(df=df)

df1 = df.copy()  # 备份一下，后面特征筛选完之后加入ds y 列用
logger.info(f"开始训练模型...")
row,col = df.shape

now = datetime.datetime.now().strftime('%Y%m%d%H%M%S')




In [ ]:
model_results3 = model_losss(sqlitedb)


In [ ]:

import matplotlib.dates as mdates

def brent_export_pdf(num_indicators=475,num_models=21, num_dayindicator=202,inputsize=5,dataset='dataset',time = '2024-07-30',reportname='report.pdf',sqlitedb='jbsh_yuanyou.db'):    
    global y
    # 创建内容对应的空列表
    content = list()
    # 获取特征的近一月值
    import pandas as pd
    feature_data_df = pd.read_csv(f'dataset/指标数据添加时间特征.csv', parse_dates=['ds']).tail(20)
    def draw_feature_trend(feature_data_df, features):
            # 画特征近一周的趋势图
            feature_df = feature_data_df[['ds','y']+features]
            # 遍历X每一列，和yy画散点图 ，
            
            for i, col in enumerate(features):
                # try:
                print(f'正在绘制第{i+1}个特征{col}与价格散点图...')
                if col not in ['ds', 'y']:
                    fig, ax1 = plt.subplots(figsize=(10, 6))
                    # 在第一个坐标轴上绘制数据
                    sns.lineplot(data=feature_df, x='ds', y='y', ax=ax1, color='b')
                    ax1.set_xlabel('日期')
                    ax1.set_ylabel('y', color='b')
                    ax1.tick_params('y', colors='b')
                    # 在 ax1 上添加文本显示值，添加一定的偏移避免值与曲线重叠
                    for j in range(1, len(feature_df), 2):
                        value = feature_df['y'].iloc[j]
                        date = feature_df['ds'].iloc[j]
                        offset = 1.001
                        ax1.text(date, value * offset, str(round(value, 2)), ha='center', va='bottom', color='b', fontsize=10)
                    # 创建第二个坐标轴
                    ax2 = ax1.twinx()
                    # 在第二个坐标轴上绘制数据
                    sns.lineplot(data=feature_df, x='ds', y=col, ax=ax2, color='r')
                    ax2.set_ylabel(col, color='r')
                    ax2.tick_params('y', colors='r')
                    # 在 ax2 上添加文本显示值，添加一定的偏移避免值与曲线重叠
                    for j in range(0, len(feature_df), 2):
                        value = feature_df[col].iloc[j]
                        date = feature_df['ds'].iloc[j]
                        offset = 1.0003
                        ax2.text(date, value * offset, str(round(value, 2)), ha='center', va='bottom', color='r', fontsize=10)
                    # 添加标题
                    plt.title(col)
                    # 设置横坐标为日期格式并自动调整
                    locator = mdates.AutoDateLocator()
                    formatter = mdates.AutoDateFormatter(locator)
                    ax1.xaxis.set_major_locator(locator)
                    ax1.xaxis.set_major_formatter(formatter)
                    # 文件名特殊字符处理
                    col = col.replace('*', '-')
                    col = col.replace(':', '-')
                    col = col.replace(r'/', '-')
                    plt.savefig(os.path.join(dataset, f'{col}与价格散点图.png'))
                    content.append(Graphs.draw_img(os.path.join(dataset, f'{col}与价格散点图.png')))
                    plt.close()
                # except Exception as e:
                #     print(f'绘制第{i+1}个特征{col}与价格散点图时出错：{e}')
            
            
            
    ### 添加标题
    content.append(Graphs.draw_title(f'{y}{time}预测报告'))

    ### 预测结果
    content.append(Graphs.draw_little_title('一、预测结果：'))
    # 添加图片
    # 找出后缀是历史价格-预测值.png的图片
    # import glob
    # imgs = glob.glob(os.path.join(dataset,'*历史价格-预测值.png'))
    # for img in imgs:
    #     content.append(Graphs.draw_img(img))
    content.append(Graphs.draw_img(os.path.join(dataset,'历史价格-预测值.png')))

    # 取df中y列为空的行
    import pandas as pd
    df = pd.read_csv(os.path.join(dataset,'predict.csv'),encoding='gbk') 
    df_true = pd.read_csv(os.path.join(dataset,'指标数据添加时间特征.csv'),encoding='utf-8')  # 获取预测日期对应的真实值
    df_true = df_true[['ds','y']]
    eval_df = pd.read_csv(os.path.join(dataset,'model_evaluation.csv'),encoding='utf-8') 
    # 按评估指标排序，取前五
    fivemodels_list = eval_df['模型(Model)'].values  # 列表形式，后面当作列名索引使用
    # 取 fivemodels_list 和 ds 列
    df = df[['ds'] + fivemodels_list.tolist() ]
    # 拼接预测日期对应的真实值
    df = pd.merge(df, df_true, on='ds', how='left')
    # 删除全部为nan的列
    df = df.dropna(how='all', axis=1)
    # 选择除 'ds' 列外的数值列，并进行类型转换和四舍五入
    num_cols = [col for col in df.columns if col!= 'ds' and pd.api.types.is_numeric_dtype(df[col])]
    for col in num_cols:
        df[col] = df[col].astype(float).round(2)
    # 添加最大值、最小值、平均值三列
    df['平均值'] = df[num_cols].mean(axis=1).round(2)
    df['最大值'] = df[num_cols].max(axis=1)
    df['最小值'] = df[num_cols].min(axis=1)
    # df转置
    df = df.T
    # df重置索引
    df = df.reset_index()
    # 添加预测值表格
    data = df.values.tolist()
    col_width = 500/len(df.columns)
    content.append(Graphs.draw_table(col_width,*data))
    content.append(Graphs.draw_little_title('二、上一预测周期偏差率分析：'))
    df = pd.read_csv(os.path.join(dataset,'testandpredict_groupby.csv'),encoding='utf-8')
    df4 = df.copy() # 计算偏差率使用
    # 计算模型偏差率
    #计算各列对于y列的差值百分比
    df3 = pd.DataFrame()  # 存储偏差率
    
    # 删除有null的行
    df4 = df4.dropna()
    df3['ds'] = df4['ds']
    for col in fivemodels_list:
        df3[col] = round(abs(df4[col] - df4['y']) / df4['y'] * 100,2)  
    # 找出决定系数前五的偏差率
    df3 = df3[['ds']+fivemodels_list.tolist()][-inputsize:]
    # 找出上一预测区间的时间
    stime = df3['ds'].iloc[0]
    etime = df3['ds'].iloc[-1]
    # 添加偏差率表格
    fivemodels = '、'.join(eval_df['模型(Model)'].values[:5]) # 字符串形式，后面写入字符串使用
    content.append(Graphs.draw_text(f'预测使用了{num_models}个模型进行训练，使用评估结果MAE前五的模型分别是 {fivemodels} ，模型上一预测区间 {stime} -- {etime}的偏差率(%)分别是：'))
    # # 添加偏差率表格
    df3 = df3.T
    df3 = df3.reset_index()
    data = df3.values.tolist()
    col_width = 500/len(df3.columns)
    content.append(Graphs.draw_table(col_width,*data))


    content.append(Graphs.draw_little_title('三、预测过程解析：'))
    ### 特征、模型、参数配置
    content.append(Graphs.draw_little_title('模型选择：'))
    content.append(Graphs.draw_text(f'本次预测使用了一个专门收集时间序列的NeuralForecast库中的{num_models}个模型：'))
    content.append(Graphs.draw_text(f'使用40天的数据预测未来{inputsize}天的数据。'))
    content.append(Graphs.draw_little_title('指标情况：'))
    with open(os.path.join(dataset,'特征频度统计.txt'),encoding='utf-8') as f:
        for line in f.readlines():
            content.append(Graphs.draw_text(line))

    data = pd.read_csv(os.path.join(dataset,'指标数据添加时间特征.csv'),encoding='utf-8') # 计算相关系数用
    df_zhibiaofenlei = loadcsv(os.path.join(dataset,'特征处理后的指标名称及分类.csv')) # 气泡图用
    df_zhibiaoshuju = data.copy()  # 气泡图用

    # 绘制特征相关气泡图
    content.append(Graphs.draw_text('气泡图中，横轴为指标名称，纵轴为指标名称，面积越大表示相关性越大，面积越小表示相关性越小。'))
    grouped = df_zhibiaofenlei.groupby('指标分类')
    grouped_corr = pd.DataFrame(columns=['指标分类', '指标数量', '相关性总和'])
    
    content.append(Graphs.draw_little_title('按指标分类分别与预测目标进行皮尔逊相关系数分析：'))
    content.append(Graphs.draw_text('''皮尔逊相关系数说明：''')) 
    content.append(Graphs.draw_text('''衡量两个特征之间的线性相关性。''')) 
    content.append(Graphs.draw_text('''
    相关系数为1：表示两个变量之间存在完全正向的线性关系，即当一个变量增加时，另一个变量也相应增加，且变化是完全一致的。''')) 
    content.append(Graphs.draw_text('''相关系数为-1：表示两个变量之间存在完全负向的线性关系，即当一个变量增加时，另一个变量会相应减少，且变化是完全相反的''')) 
    content.append(Graphs.draw_text('''相关系数接近0：表示两个变量之间不存在线性关系，即它们的变化不会随着对方的变化而变化。''')) 
    for name, group in grouped:
        cols = group['指标名称'].tolist()
        logger.info(f'开始绘制{name}类指标的相关性直方图')
        cols_subset = cols
        feature_names = ['y'] + cols_subset
        correlation_matrix = df_zhibiaoshuju[feature_names].corr()['y']

        # 绘制特征相关性直方分布图
        plt.figure(figsize=(10,8))
        sns.histplot(correlation_matrix.values.flatten(), bins=20, kde=True, color='skyblue')
        plt.title(f'{name}类指标(共{len(cols_subset)}个)相关性直方分布图')
        plt.xlabel('相关系数')
        plt.ylabel('频数')
        plt.savefig(os.path.join(dataset, f'{name}类指标相关性直方分布图.png'), bbox_inches='tight')
        plt.close()
        content.append(Graphs.draw_img(os.path.join(dataset,f'{name}类指标相关性直方分布图.png')))
        content.append(Graphs.draw_text(f'{name}类指标(共{len(cols_subset)}个)的相关性直方分布图如上所示。'))
        # 相关性大于0的特征
        positive_corr_features = correlation_matrix[correlation_matrix > 0].sort_values(ascending=False).index.tolist()[1:]
        
        print(f'{name}下正相关的特征值有：',positive_corr_features)
        if len(positive_corr_features) > 5:
            positive_corr_features = positive_corr_features[0:5]
            content.append(Graphs.draw_text(f'{name}类指标中，与预测目标y正相关前五的特征有：{positive_corr_features}'))
            draw_feature_trend(feature_data_df, positive_corr_features)
        elif len(positive_corr_features) == 0:
            pass
        else:
            positive_corr_features = positive_corr_features
            content.append(Graphs.draw_text(f'其中，与预测目标y正相关的特征有：{positive_corr_features}'))
            draw_feature_trend(feature_data_df, positive_corr_features)
        
        # 相关性小于0的特征
        negative_corr_features = correlation_matrix[correlation_matrix < 0].sort_values(ascending=True).index.tolist()
        
        print(f'{name}下负相关的特征值有：',negative_corr_features)
        if len(negative_corr_features) > 5:
            negative_corr_features = negative_corr_features[:5]
            content.append(Graphs.draw_text(f'与预测目标y负相关前五的特征有：{negative_corr_features}'))
            draw_feature_trend(feature_data_df, negative_corr_features)
        elif len(negative_corr_features) == 0:
            pass
        else:
            content.append(Graphs.draw_text(f'{name}类指标中，与预测目标y负相关的特征有：{negative_corr_features}'))
            draw_feature_trend(feature_data_df, negative_corr_features)
        
        
        # 计算correlation_sum 第一行的相关性的绝对值的总和
        correlation_sum = correlation_matrix.abs().sum()
        logger.info(f'{name}类指标的相关性总和为：{correlation_sum}')
        # 分组的相关性总和拼接到grouped_corr
        goup_corr = pd.DataFrame({'指标分类': [name], '指标数量': [len(cols_subset)], '相关性总和': [correlation_sum]})
        grouped_corr = pd.concat([grouped_corr, goup_corr], axis=0, ignore_index=True)

    # 绘制相关性总和的气泡图
    logger.info(f'开始绘制相关性总和的气泡图')
    plt.figure(figsize=(10, 10))
    sns.scatterplot(data=grouped_corr, x='相关性总和', y='指标数量', size='相关性总和', sizes=(grouped_corr['相关性总和'].min()*5, grouped_corr['相关性总和'].max()*5), hue='指标分类', palette='viridis')
    plt.title('指标分类相关性总和的气泡图')
    plt.ylabel('数量')
    plt.savefig(os.path.join(dataset, '指标分类相关性总和的气泡图.png'), bbox_inches='tight')
    plt.close()
    content.append(Graphs.draw_img(os.path.join(dataset,'指标分类相关性总和的气泡图.png')))
    logger.info(f'绘制相关性总和的气泡图结束')
    


    # # 计算特征相关性
    # data.rename(columns={y: 'y'}, inplace=True)  
    # data['ds'] = pd.to_datetime(data['ds'])  
    # data.drop(columns=['ds'], inplace=True)
    # # 创建一个空的 DataFrame 来保存相关系数
    # correlation_df = pd.DataFrame(columns=['Feature', 'Correlation'])
    # # 计算各特征与目标列的皮尔逊相关系数，并保存到新的 Data 中
    # for col in data.columns:
    #     if col!= 'y':
    #         pearson_correlation = np.corrcoef(data[col], data['y'])[0, 1]
    #         spearman_correlation, _ = spearmanr(data[col], data['y'])
    #         new_row = {'Feature': col, 'Pearson_Correlation': round(pearson_correlation,3), 'Spearman_Correlation': round(spearman_correlation,2)}
    #         correlation_df = correlation_df._append(new_row, ignore_index=True)

    # correlation_df.drop('Correlation', axis=1, inplace=True)
    # correlation_df.dropna(inplace=True)
    # correlation_df.to_csv(os.path.join(dataset,'指标相关性分析.csv'), index=False)

    # data = correlation_df['Pearson_Correlation'].values.tolist()
    # # 生成 -1 到 1 的 20 个区间
    # bins = np.linspace(-1, 1, 21)
    # # 计算每个区间的统计数（这里是区间内数据的数量）
    # hist_values = [np.sum((data >= bins[i]) & (data < bins[i + 1])) for i in range(len(bins) - 1)]

    # #设置画布大小
    # plt.figure(figsize=(10, 6))
    # # 绘制直方图
    # plt.bar(bins[:-1], hist_values, width=(bins[1] - bins[0]))

    # # 添加标题和坐标轴标签
    # plt.title('皮尔逊相关系数分布图')
    # plt.xlabel('区间')
    # plt.ylabel('统计数')
    # plt.savefig(os.path.join(dataset, '皮尔逊相关性系数.png'))
    # plt.close()


    # #设置画布大小
    # plt.figure(figsize=(10, 6))
    # data = correlation_df['Spearman_Correlation'].values.tolist()
    # # 计算每个区间的统计数（这里是区间内数据的数量）
    # hist_values = [np.sum((data >= bins[i]) & (data < bins[i + 1])) for i in range(len(bins) - 1)]

    # # 绘制直方图
    # plt.bar(bins[:-1], hist_values, width=(bins[1] - bins[0]))

    # # 添加标题和坐标轴标签
    # plt.title('斯皮尔曼相关系数分布图')
    # plt.xlabel('区间')
    # plt.ylabel('统计数')
    # plt.savefig(os.path.join(dataset, '斯皮尔曼相关性系数.png'))
    # plt.close()
    # content.append(Graphs.draw_text(f'指标相关性分析--皮尔逊相关系数：'))
    # # 皮尔逊正相关 不相关  负相关 的表格
    # content.append(Graphs.draw_img(os.path.join(dataset,'皮尔逊相关性系数.png')))
    # content.append(Graphs.draw_text('''皮尔逊相关系数说明：''')) 
    # content.append(Graphs.draw_text('''衡量两个特征之间的线性相关性。''')) 
    # content.append(Graphs.draw_text('''
    # 相关系数为1：表示两个变量之间存在完全正向的线性关系，即当一个变量增加时，另一个变量也相应增加，且变化是完全一致的。''')) 
    # content.append(Graphs.draw_text('''当前特征中正相关前十的有：''')) 
    # top10_columns = correlation_df.sort_values(by='Pearson_Correlation',ascending=False).head(10)['Feature'].to_list()
    # top10 = ','.join(top10_columns)
    # content.append(Graphs.draw_text(f'''{top10}''')) 

    # feature_df = feature_data_df[['ds','y']+top10_columns]
    # # 遍历X每一列，和yy画散点图 ，
    # for i, col in enumerate(feature_df.columns):
    #     print(f'正在绘制第{i+1}个特征{col}与价格散点图...')
    #     if col not in ['ds', 'y']:
    #         fig, ax1 = plt.subplots(figsize=(10, 6))
    #         # 在第一个坐标轴上绘制数据
    #         ax1.plot(feature_df['ds'], feature_df['y'], 'b-')
    #         ax1.set_xlabel('日期')
    #         ax1.set_ylabel('y', color='b')
    #         ax1.tick_params('y', colors='b')
    #         # 在 ax1 上添加文本显示值，添加一定的偏移避免值与曲线重叠
    #         for j in range(1,len(feature_df),2):
    #             value = feature_df['y'].iloc[j]
    #             date = feature_df['ds'].iloc[j]
    #             offset = 1.001
    #             ax1.text(date, value * offset, str(round(value, 2)), ha='center', va='bottom', color='b', fontsize=10)
    #         # 创建第二个坐标轴
    #         ax2 = ax1.twinx()
    #         # 在第二个坐标轴上绘制数据
    #         line2 = ax2.plot(feature_df['ds'], feature_df[col], 'r-')
    #         ax2.set_ylabel(col, color='r')
    #         ax2.tick_params('y', colors='r')
    #         # 在 ax2 上添加文本显示值，添加一定的偏移避免值与曲线重叠
    #         for j in range(0,len(feature_df),2):
    #             value = feature_df[col].iloc[j]
    #             date = feature_df['ds'].iloc[j]
    #             offset = 1.001
    #             ax2.text(date, value * offset, str(round(value, 2)), ha='center', va='bottom', color='r', fontsize=10)
    #         # 添加标题
    #         plt.title(col)
    #         # 设置横坐标为日期格式并自动调整
    #         locator = mdates.AutoDateLocator()
    #         formatter = mdates.AutoDateFormatter(locator)
    #         ax1.xaxis.set_major_locator(locator)
    #         ax1.xaxis.set_major_formatter(formatter)
    #         # 文件名特殊字符处理
    #         col = col.replace('*', '-')
    #         col = col.replace(':', '-')
    #         plt.savefig(os.path.join(dataset, f'{col}与价格散点图.png'))
    #         content.append(Graphs.draw_img(os.path.join(dataset, f'{col}与价格散点图.png')))
    #         plt.close()


    # content.append(Graphs.draw_text(f'指标相关性分析--斯皮尔曼相关系数：'))
    # # 皮尔逊正相关 不相关  负相关 的表格
    # content.append(Graphs.draw_img(os.path.join(dataset,'斯皮尔曼相关性系数.png')))
    # content.append(Graphs.draw_text('斯皮尔曼相关系数（Spearmans rank correlation coefficient）是一种用于衡量两个变量之间的单调关系（不一定是线性关系）的统计指标。'))
    # content.append(Graphs.draw_text('它的计算基于变量的秩次（即变量值的排序位置）而非变量的原始值。'))
    # content.append(Graphs.draw_text('斯皮尔曼相关系数的取值范围在 -1 到 1 之间。'))
    # content.append(Graphs.draw_text('当系数为 1 时，表示两个变量之间存在完全正的单调关系；'))
    # content.append(Graphs.draw_text('''当前特征中正单调关系前十的有：''')) 
    # top10_columns = correlation_df.sort_values(by='Spearman_Correlation',ascending=False).head(10)['Feature'].to_list()
    # top10 = ','.join(top10_columns)
    # content.append(Graphs.draw_text(f'''{top10}''')) 

    # feature_df = feature_data_df[['ds','y']+top10_columns]
    # # 遍历X每一列，和yy画散点图 ，
    # for i, col in enumerate(feature_df.columns):
    #     print(f'正在绘制第{i+1}个特征{col}与价格散点图...')
    #     if col not in ['ds', 'y']:
    #         fig, ax1 = plt.subplots(figsize=(10, 6))
    #         # 在第一个坐标轴上绘制数据
    #         ax1.plot(feature_df['ds'], feature_df['y'], 'b-')
    #         ax1.set_xlabel('日期')
    #         ax1.set_ylabel('y', color='b')
    #         ax1.tick_params('y', colors='b')
    #         # 在 ax1 上添加文本显示值，添加一定的偏移避免值与曲线重叠
    #         for j in range(1,len(feature_df),2):
    #             value = feature_df['y'].iloc[j]
    #             date = feature_df['ds'].iloc[j]
    #             offset = 1.001
    #             ax1.text(date, value * offset, str(round(value, 2)), ha='center', va='bottom', color='b', fontsize=10)
    #         # 创建第二个坐标轴
    #         ax2 = ax1.twinx()
    #         # 在第二个坐标轴上绘制数据
    #         line2 = ax2.plot(feature_df['ds'], feature_df[col], 'r-')
    #         ax2.set_ylabel(col, color='r')
    #         ax2.tick_params('y', colors='r')
    #         # 在 ax2 上添加文本显示值，添加一定的偏移避免值与曲线重叠
    #         for j in range(0,len(feature_df),2):
    #             value = feature_df[col].iloc[j]
    #             date = feature_df['ds'].iloc[j]
    #             offset = 1.001
    #             ax2.text(date, value * offset, str(round(value, 2)), ha='center', va='bottom', color='r', fontsize=10)
    #         # 添加标题
    #         plt.title(col)
    #         # 设置横坐标为日期格式并自动调整
    #         locator = mdates.AutoDateLocator()
    #         formatter = mdates.AutoDateFormatter(locator)
    #         ax1.xaxis.set_major_locator(locator)
    #         ax1.xaxis.set_major_formatter(formatter)
    #         # 文件名特殊字符处理
    #         col = col.replace('*', '-')
    #         col = col.replace(':', '-')
    #         plt.savefig(os.path.join(dataset, f'{col}与价格散点图.png'))
    #         content.append(Graphs.draw_img(os.path.join(dataset, f'{col}与价格散点图.png')))
    #         plt.close()

    # content.append(Graphs.draw_text('当系数为 -1 时，表示存在完全负的单调关系；'))
    # content.append(Graphs.draw_text('''当前特征中负单调关系前十的有：''')) 
    # tail10_columns = correlation_df.sort_values(by='Spearman_Correlation',ascending=True).head(10)['Feature'].to_list()
    # top10 = ','.join(tail10_columns)
    # content.append(Graphs.draw_text(f'''{top10}''')) 
    # # 获取特征的近一周值
    # feature_df = feature_data_df[['ds','y']+tail10_columns]
    # # 遍历X每一列，和yy画散点图 ，
    # for i, col in enumerate(feature_df.columns):
    #     print(f'正在绘制第{i+1}个特征{col}与价格散点图...')
    #     if col not in ['ds', 'y']:
    #         fig, ax1 = plt.subplots(figsize=(10, 6))
    #         # 在第一个坐标轴上绘制数据
    #         ax1.plot(feature_df['ds'], feature_df['y'], 'b-')
    #         ax1.set_xlabel('日期')
    #         ax1.set_ylabel('y', color='b')
    #         ax1.tick_params('y', colors='b')
    #         # 在 ax1 上添加文本显示值，添加一定的偏移避免值与曲线重叠
    #         for j in range(len(feature_df)):
    #             if j%2 == 1:
    #                 value = feature_df['y'].iloc[j]
    #                 date = feature_df['ds'].iloc[j]
    #                 offset = 1.001
    #                 ax1.text(date, value * offset, str(round(value, 2)), ha='center', va='bottom', color='b', fontsize=10)
    #         # 创建第二个坐标轴
    #         ax2 = ax1.twinx()
    #         # 在第二个坐标轴上绘制数据
    #         line2 = ax2.plot(feature_df['ds'], feature_df[col], 'r-')
    #         ax2.set_ylabel(col, color='r')
    #         ax2.tick_params('y', colors='r')
    #         # 在 ax2 上添加文本显示值，添加一定的偏移避免值与曲线重叠
    #         for j in range(1,len(feature_df),2):
    #             value = feature_df[col].iloc[j]
    #             date = feature_df['ds'].iloc[j]
    #             offset = 1.001
    #             ax2.text(date, value * offset, str(round(value, 2)), ha='center', va='bottom', color='r', fontsize=10)
    #         # 添加标题
    #         plt.title(col)
    #         # 设置横坐标为日期格式并自动调整
    #         locator = mdates.AutoDateLocator()
    #         formatter = mdates.AutoDateFormatter(locator)
    #         ax1.xaxis.set_major_locator(locator)
    #         ax1.xaxis.set_major_formatter(formatter)
    #         # 文件名特殊字符处理
    #         col = col.replace('*', '-')
    #         col = col.replace(':', '-')
    #         plt.savefig(os.path.join(dataset, f'{col}与价格散点图.png'))
    #         content.append(Graphs.draw_img(os.path.join(dataset, f'{col}与价格散点图.png')))
    #         plt.close()
    # content.append(Graphs.draw_text('当系数为 0 时，表示两个变量之间不存在单调关系。'))
    # content.append(Graphs.draw_text('与皮尔逊相关系数相比，斯皮尔曼相关系数对于数据中的异常值不敏感，更适用于处理非线性关系或存在极端值的数据。'))
    content.append(Graphs.draw_little_title('模型选择：'))
    content.append(Graphs.draw_text(f'预测使用了{num_models}个模型进行训练拟合，通过评估指标MAE从小到大排列，前5个模型的简介如下：'))

    ### 读取模型简介
    with open(os.path.join(dataset,'model_introduction.txt'), 'r', encoding='utf-8') as f:
        for line in f:
            line_split = line.strip().split('--')
            if line_split[0] in fivemodels_list:
                for introduction in line_split:
                    content.append(Graphs.draw_text(introduction))

    content.append(Graphs.draw_little_title('模型评估：'))
    
    df = pd.read_csv(os.path.join(dataset,'model_evaluation.csv'),encoding='utf-8') 
    # 判断 df 的数值列转为float
    for col in eval_df.columns:
        if col not in ['模型(Model)']:
            eval_df[col] = eval_df[col].astype(float)
            eval_df[col] = eval_df[col].round(3)
    # 筛选 fivemodels_list.tolist()  的行
    eval_df = eval_df[eval_df['模型(Model)'].isin(fivemodels_list)]
    # df转置
    eval_df = eval_df.T
    # df重置索引
    eval_df = eval_df.reset_index()
    eval_df = eval_df.T
    # # 添加表格
    data = eval_df.values.tolist()
    col_width = 500/len(eval_df.columns)
    content.append(Graphs.draw_table(col_width,*data))
    content.append(Graphs.draw_text('评估指标释义：'))
    content.append(Graphs.draw_text('1. 均方根误差(RMSE)：均方根误差是衡量预测值与实际值之间误差的一种方法，取值越小，误差越小，预测效果越好。'))
    content.append(Graphs.draw_text('2. 平均绝对误差(MAE)：平均绝对误差是衡量预测值与实际值之间误差的一种方法，取值越小，误差越小，预测效果越好。'))
    content.append(Graphs.draw_text('3. 平均平方误差(MSE)：平均平方误差是衡量预测值与实际值之间误差的一种方法，取值越小，误差越小，预测效果越好。'))
    content.append(Graphs.draw_text('模型拟合：'))
    # 添加图片
    content.append(Graphs.draw_img(os.path.join(dataset,'预测值与真实值对比图.png')))

    # 附1，特征列表
    content.append(Graphs.draw_little_title('附1、特征列表：'))
    df_fuyi = pd.read_csv(os.path.join(dataset,'特征频度统计.csv'),encoding='utf-8') 
    for col in df_fuyi.columns:
        fuyi = df_fuyi[col]
        fuyi = fuyi.dropna()
        content.append(Graphs.draw_text(f'{col}：'))
        for i in range(len(fuyi)):
            content.append(Graphs.draw_text(f'{i+1}、{fuyi[i]}'))
    


    ### 生成pdf文件
    doc = SimpleDocTemplate(os.path.join(dataset,reportname), pagesize=letter)
    # doc = SimpleDocTemplate(os.path.join(dataset,'reportname.pdf'), pagesize=letter)
    doc.build(content)
    # pdf 上传到数字化信息平台
    # 读取pdf并转为base64
    try:
        if is_update_report:
            with open(os.path.join(dataset,reportname), 'rb') as f:
                base64_data = base64.b64encode(f.read()).decode('utf-8')
                upload_data["data"]["fileBase64"] = base64_data
            upload_data["data"]["fileName"] = reportname
            token = get_head_auth_report()
            upload_report_data(token, upload_data)
    except TimeoutError as e:
        print(f"请求超时: {e}")
        
        

In [51]:
 
title = f'{settings}--{now}-预测报告' # 报告标题
brent_export_pdf(dataset=dataset,num_models = 5 if is_fivemodels else 22,time=end_time,
            reportname=reportname,sqlitedb=sqlitedb),
# pp_export_pdf(dataset=dataset,num_models = 5 if is_fivemodels else 22,time=end_time,
            # reportname=reportname),
logger.info('模型训练完成')

开始绘制Kpler数据--原油出口类指标的相关性直方图
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):


Kpler数据--原油出口下正相关的特征值有： []
Kpler数据--原油出口下负相关的特征值有： ['Libya', 'Malaysia']
正在绘制第1个特征Libya与价格散点图...


d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating

正在绘制第2个特征Malaysia与价格散点图...


d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating

...

d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating

正在绘制第4个特征中国独立炼厂原油加工量-隆众与价格散点图...


d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating

正在绘制第5个特征美国柴油产量占比与价格散点图...


d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating